## Kelley hu4d5-5 VL-R66G charging step error analysis

In this notebook we will use a random forest model to find the most energetically influential degrees of freedom for the VL-R66G charging step TI production run. Next, we will compare the sampling of these DOF during TI production to a free energy profile derived from end state GaMD sampling. We will attempt to  correct any inaccurate sampling in the TI data and find the estimated ddG before and after the correction. 

In [1]:
import os
os.chdir("..")
from common_functions import *

### Ingesting original TI lambda production data

In [2]:
os.chdir("./TI_data/VL-R66G")
geom_dvdls_crg = pd.read_csv("R66G_crg_bound.csv")
geom_dvdls_crg_ub = pd.read_csv("R66G_crg_unbound.csv")
geom_dvdls_vdw = pd.read_csv("R66G_vdw_bound.csv")
geom_dvdls_vdw_ub = pd.read_csv("R66G_vdw_unbound.csv")


### Charging step data ingestion (unbound state)

In [ ]:
# unbound state crg
os.chdir("/gne/data/pharmr/pharmr/sastrys1/thermo-integration/kelley_struct_mutants/sunidhi_paper/hu4d5-3/charging/unbound_farCoAlc")
dvdls_crg_ub = read_rotamers(5)
sc_dih_crg_ub = pd.read_csv("./sc_all_dihedrals/sc_chis.dat", sep="\s+")

sc_dvdls_crg_ub = pd.merge(sc_dih_crg_ub, dvdls_crg_ub, left_index=True, right_index=True)

### Vdw step data ingestion (bound/unbound state)

In [ ]:
# don't need the rotamers/distances info for vdw, just the dvdl's to compute the ddG
os.chdir("/gstore/scratch/u/sastrys1/thermo-integration/kelley_struct_mutants/sunidhi_paper/hu4d5-3/vdw/bound")
dvdls_vdw = read_rotamers(5)

os.chdir("/gstore/scratch/u/sastrys1/thermo-integration/kelley_struct_mutants/sunidhi_paper/hu4d5-3/vdw/unbound")
dvdls_vdw_ub = read_rotamers(5)

### Initial VL-R66G TI ddG estimate:

In [3]:
dG_bd_crg = geom_dvdls_crg.groupby("Lambda").mean()["weight_dvdl"].sum()
dG_ubd_crg = geom_dvdls_crg_ub.groupby("Lambda").mean()["weight_dvdl"].sum()
ddG_crg = dG_bd_crg - dG_ubd_crg

dG_bd_vdw = geom_dvdls_vdw.groupby("Lambda").mean()["weight_dvdl"].sum()
dG_ubd_vdw = geom_dvdls_vdw_ub.groupby("Lambda").mean()["weight_dvdl"].sum()
ddG_vdw = dG_bd_vdw - dG_ubd_vdw

empirical_value = 0.22

print("Original ddG (crg step): ")
print(f"{round(ddG_crg, 4)} kcal/mol")

print("Original ddG (vdw step): ")
print(f"{round(ddG_vdw, 4)} kcal/mol")

print("Original total ddG: ")
print(f"{round(ddG_crg + ddG_vdw, 4)} kcal/mol")

print()
print("Empirical value: ")
print(f"{empirical_value} kcal/mol")

orig_error = abs((ddG_crg + ddG_vdw) - empirical_value)

print("Original ddG error: ")
print(f"{round(orig_error, 4)} kcal/mol")

Original ddG (crg step): 
-0.8642 kcal/mol
Original ddG (vdw step): 
0.1575 kcal/mol
Original total ddG: 
-0.7066 kcal/mol

Empirical value: 
0.22 kcal/mol
Original ddG error: 
0.9266 kcal/mol


### Charging step RF model

#### Splitting data into independent/dependent variables for random forest model

See our methods/supplemental methods section for our process to choose the input features.

In [4]:
X = geom_dvdls_crg.drop(
    ["weight_dvdl", "dvdl", "Run", "Lambda", "#Frame", "R66_T69", "R66_G68"
    ], axis=1)

X_scl = pd.DataFrame(StandardScaler().fit_transform(X))
X_scl.columns = X.columns
Y = geom_dvdls_crg["weight_dvdl"]


#### Checking for cross-correlation among independent variables

In [5]:
absCorr = abs(X_scl.corr())
for i in absCorr.columns:
    for j in absCorr.index:
        cor = absCorr.loc[i, j]
        if abs(cor) > 0.5 and i != j:
            print(i, j)
            print(cor)
            

#### Using random forest model to identify the most influential degrees of freedom

We run our model 25 times, then sort the results by the mean of feature importance across the 25 iterations. The model found that VL-V29 side chain rotamers chi1 and chi2 were the most influential nearby DOF on TI DV/DL.

In [24]:
rfeDefault = RFE(estimator=DecisionTreeRegressor(max_depth=5, random_state=42), n_features_to_select=0.75, step=0.05)
rfDefault = RandomForestRegressor(
    max_depth=10, n_estimators=200, oob_score=True, max_features=0.6, min_samples_leaf = 7, min_samples_split=14, random_state=42
)

pipelineDefault_rf = Pipeline([
    ('feature_scaling', StandardScaler()),
    ('feature_selection', rfeDefault),
    ('regression_model', rfDefault)
])


imps = benchmark_model(pipelineDefault_rf, X_scl, Y, geom_dvdls_crg["Lambda"])
imps[["Mean", "Median"]].sort_values(by="Mean", ascending=False)[:15]

Avg. training r2: 
0.757
Training r2 std dev: 
0.0014
Avg. test r2: 
0.6825
Testing r2 std dev: 
0.0043


Mean    Median
V384_chi2  0.145102  0.112211
V384_chi1  0.123891  0.044461
N385_chi1  0.098193  0.099875
D383_chi1  0.089834  0.089841
T427_chi1  0.077084  0.077223
R66_N28    0.068928  0.068840
S407_chi1  0.060139  0.060776
N385_chi2  0.058187  0.061409
S420_chi1  0.049836  0.030201
T386_chi1  0.045699  0.033033
S422_chi1  0.041889  0.051422
D425_chi2  0.035468  0.052214
R421_chi3  0.030670  0.016195
D383_chi2  0.027348  0.017724
R421_chi1  0.027315  0.019288

### Comparing the TI rotamers with the GaMD pmf (bound state)

The RF model tells us that the most energetically influential features to DV/DL are "V384_chi1" and "V384_chi2", aka VL-V29 side chain rotamers chi1 and chi2. We used GaMD on the WT hu4d5-5 complex to obtain enhanced sampling data for this end state. Then, we used PyReweighting-2D to generate a 2-D PMF of VH-V29 chi1 and VL-V29 chi2 to give us an idea of the ideal sampling of these two energetically influential features. Finally, we plot the VL-V29 rotamers explored during TI overlaid onto the GaMD pmf to probe the quality of sampling during TI.

Next, we will compare the proportion of TI sampling in each of the three predominant microstates to the relative areas of the microstates in the GaMD end state free energy profile.

In [19]:
os.chdir("../../gamd_pmfs/VL-R66G")
v164_pmf = get_pmf_2d(
    "./pmf-c2-V164c1c2_conv_300ns.dat.xvg"
)

geom_dvdls_crg["in_pmf_cont"] = rot_in_pmf_cont(geom_dvdls_crg, "V384_chi1", "V384_chi2", v164_pmf, 10)

In [9]:
fig = plot_pmf_with_TI_2d_fig(v164_pmf, geom_dvdls_crg[geom_dvdls_crg["in_pmf_cont"]], "V384_chi1", "V384_chi2")
fig.update_layout(width=1000, height=700)
fig.show(renderer="svg")

### Checking sampling of the three microstates

The first microstate (leftmost) has insufficient sampling in many lambdas. We will run more TI lambda production with starting rotamers specifically in this microstate to boost sampling.

In [20]:
print(geom_dvdls_crg[
    (geom_dvdls_crg["in_pmf_cont"]) &
    (geom_dvdls_crg["V384_chi1"] > -120) &
    (geom_dvdls_crg["V384_chi1"] < -25)      
].groupby("Lambda").count()["weight_dvdl"])

print(geom_dvdls_crg[
    (geom_dvdls_crg["in_pmf_cont"]) &
    (geom_dvdls_crg["V384_chi1"] > 0) &
    (geom_dvdls_crg["V384_chi1"] < 120)      
].groupby("Lambda").count()["weight_dvdl"])

print(geom_dvdls_crg[
    (geom_dvdls_crg["in_pmf_cont"]) &
    (geom_dvdls_crg["V384_chi1"] > 120) |
    (geom_dvdls_crg["V384_chi1"] < -150)      
].groupby("Lambda").count()["weight_dvdl"])

Lambda
1      13
2     178
3     158
4      86
5       5
8      70
9     350
10    332
11     69
12    112
Name: weight_dvdl, dtype: int64
Lambda
1     443
2     454
3     394
4     215
5     202
6     288
7     560
8     394
9     160
10    167
11    340
12    196
Name: weight_dvdl, dtype: int64
Lambda
1     533
2     295
3     400
4     665
5     780
6     695
7     421
8     486
9     400
10    399
11    544
12    630
Name: weight_dvdl, dtype: int64


### Ingesting boosted TI lambda production sampling on the leftmost state

In [12]:
os.chdir("../../TI_data/VL-R66G")
geom_dvdls_boost = pd.read_csv("R66G_crg_boosted.csv")

geom_dvdls_boost["in_pmf_cont"] = rot_in_pmf_cont(geom_dvdls_boost, "V384_chi1", "V384_chi2", v164_pmf, 10)

#### Checking the sampling on the microstates to make sure it is sufficient

In [42]:
st1 = geom_dvdls_boost[
    (geom_dvdls_boost["in_pmf_cont"]) &
    (geom_dvdls_boost["V384_chi1"] > -150) &
    (geom_dvdls_boost["V384_chi1"] < -25)      
]

st2 = geom_dvdls_boost[
    (geom_dvdls_boost["in_pmf_cont"]) &
    (geom_dvdls_boost["V384_chi1"] > 0) &
    (geom_dvdls_boost["V384_chi1"] < 120)      
]

st3 = geom_dvdls_boost[
    (geom_dvdls_boost["in_pmf_cont"]) &
    ((geom_dvdls_boost["V384_chi1"] > 120) |
    (geom_dvdls_boost["V384_chi1"] < -150))    
]

print(st1.groupby("Lambda").count()["weight_dvdl"])
print(st2.groupby("Lambda").count()["weight_dvdl"])
print(st3.groupby("Lambda").count()["weight_dvdl"])

dG_st1 = st1.groupby("Lambda").mean().sum()["weight_dvdl"]
dG_st2 = st2.groupby("Lambda").mean().sum()["weight_dvdl"]
dG_st3 = st3.groupby("Lambda").mean().sum()["weight_dvdl"]

Lambda
1     1151
2     1208
3     1634
4     1075
5      209
6      234
7       94
8      355
9      502
10     390
11     981
12     747
Name: weight_dvdl, dtype: int64
Lambda
1      643
2     1019
3      493
4      592
5     1626
6      731
7     1298
8      951
9     1794
10    1850
11     680
12     386
Name: weight_dvdl, dtype: int64
Lambda
1      829
2      415
3      432
4      977
5     1007
6     1851
7     1502
8     1541
9      484
10     580
11     892
12    1395
Name: weight_dvdl, dtype: int64


### Comparing TI sampling of the three microstates to the GaMD free energy profile areas

In [55]:

a1 = v164_pmf[(v164_pmf["X"] > -120) & (v164_pmf["X"] < -25)]["pop"].sum()
a2 = v164_pmf[(v164_pmf["X"] > 0) & (v164_pmf["X"] < 120)]["pop"].sum()
a3 = v164_pmf[(v164_pmf["X"] > 120) | (v164_pmf["X"] < -150)]["pop"].sum()

a1_prop = a1/(a1 + a2 + a3)
a2_prop = a2/(a1 + a2 + a3)
a3_prop = a3/(a1 + a2 + a3)

print("GaMD pmf left hand state proportion: ")
print(round(a1_prop, 4))
print("GaMD pmf middle state proportion: ")
print(round(a2_prop, 4))
print("GaMD pmf right hand state proportion: ")
print(round(a3_prop, 4))


ti1 = len(st1)
ti2 = len(st2)
ti3 = len(st3)

print("TI left hand state proportion: ")
print(round(ti1/(ti1 + ti2 + ti3), 4))
print("TI middle hand state proportion: ")
print(round(ti2/(ti1 + ti2 + ti3), 4))
print("TI right hand state proportion: ")
print(round(ti3/(ti1 + ti2 + ti3), 4))


GaMD pmf left hand state proportion: 
0.0963
GaMD pmf middle state proportion: 
0.2731
GaMD pmf right hand state proportion: 
0.6306
TI left hand state proportion: 
0.2636
TI middle hand state proportion: 
0.3706
TI right hand state proportion: 
0.3658


### Recomputing charging step bound state dG

In [56]:
dG_corr = a1_prop * dG_st1 + a2_prop * dG_st2 + a3_prop * dG_st3
print(dG_corr)

302.7004999438085


### Comparing GaMD with TI, unbound state

In [57]:
os.chdir("../../gamd_pmfs/VL-R66G")
v164_pmf_ub = get_pmf_2d(
    "./pmf-c2-V29c1c2_conv_300ns.dat.xvg"
)

geom_dvdls_crg_ub["in_pmf_cont"] = rot_in_pmf_cont(geom_dvdls_crg_ub, "V249_chi1", "V249_chi2", v164_pmf_ub, 10)


In [58]:
fig = plot_pmf_with_TI_2d_fig(v164_pmf_ub, geom_dvdls_crg_ub[geom_dvdls_crg_ub["in_pmf_cont"]], "V249_chi1", "V249_chi2")
fig.update_layout(width=1000, height=700)
fig.show(renderer="svg")

### Checking sampling of the three microstates

The leftmost and rightmost microstates have insufficient sampling and need boosted TI lambda production sampling.

In [60]:
print(geom_dvdls_crg_ub[
    (geom_dvdls_crg_ub["in_pmf_cont"]) &
    (geom_dvdls_crg_ub["V249_chi1"] > -100) & 
    (geom_dvdls_crg_ub["V249_chi1"] < -25) 
].groupby("Lambda").count()["weight_dvdl"])

print(geom_dvdls_crg_ub[
    (geom_dvdls_crg_ub["in_pmf_cont"]) &
    (geom_dvdls_crg_ub["V249_chi1"] > 0) & 
    (geom_dvdls_crg_ub["V249_chi1"] < 100)
].groupby("Lambda").count()["weight_dvdl"])

print(geom_dvdls_crg_ub[
    (geom_dvdls_crg_ub["in_pmf_cont"]) &
    ((geom_dvdls_crg_ub["V249_chi1"] > 125) | 
    (geom_dvdls_crg_ub["V249_chi1"] < -100))
].groupby("Lambda").count()["weight_dvdl"])

Lambda
1     133
4       5
7      16
8       9
9     179
10    164
12     56
Name: weight_dvdl, dtype: int64
Lambda
1     411
2     547
3     822
4     700
5     882
6     880
7     749
8     874
9     721
10    723
11    866
12    650
Name: weight_dvdl, dtype: int64
Lambda
1     416
2     410
3     138
4     246
5      75
6      60
7     144
8      30
9      29
10     33
11     61
12    221
Name: weight_dvdl, dtype: int64


### Ingesting boosted TI lambda production sampling on the leftmost and rightmost states

In [61]:
os.chdir("../../TI_data/VL-R66G")
sc_dvdls_crgUb_boost = pd.read_csv("R66G_crg_boost_ub.csv")

In [62]:
# sc_dvdls_crgUb_boost = pd.concat([geom_dvdls_crg_ub, sc_dvdls_crg_ub_more_st1, sc_dvdls_crg_ub_more_st1_2, sc_dvdls_crg_ub_more_st3])
sc_dvdls_crgUb_boost["in_pmf_cont"] = rot_in_pmf_cont(sc_dvdls_crgUb_boost, "V249_chi1", "V249_chi2", v164_pmf_ub, 10)


In [63]:
st1_ub = sc_dvdls_crgUb_boost[
    (sc_dvdls_crgUb_boost["in_pmf_cont"]) &
    (sc_dvdls_crgUb_boost["V249_chi1"] > -100) & 
    (sc_dvdls_crgUb_boost["V249_chi1"] < -25) 
]

st2_ub = sc_dvdls_crgUb_boost[
    (sc_dvdls_crgUb_boost["in_pmf_cont"]) &
    (sc_dvdls_crgUb_boost["V249_chi1"] > 0) & 
    (sc_dvdls_crgUb_boost["V249_chi1"] < 100)
]

st3_ub = sc_dvdls_crgUb_boost[
    (sc_dvdls_crgUb_boost["in_pmf_cont"]) &
    (sc_dvdls_crgUb_boost["V249_chi1"] > 125) | 
    (sc_dvdls_crgUb_boost["V249_chi1"] < -150)
]


### Checking that the sampling is now sufficient

In [64]:
print(st1_ub.groupby("Lambda").count()["weight_dvdl"])
dG_st1_ub = st1_ub.groupby("Lambda").mean().sum()["weight_dvdl"]

print(st2_ub.groupby("Lambda").count()["weight_dvdl"])
dG_st2_ub = st2_ub.groupby("Lambda").mean().sum()["weight_dvdl"]

print(st3_ub.groupby("Lambda").count()["weight_dvdl"])
dG_st3_ub = st3_ub.groupby("Lambda").mean().sum()["weight_dvdl"]

Lambda
1     1272
2     1319
3      197
4      201
5      138
6      500
7      315
8      268
9     1447
10    1781
11    1563
12    1084
Name: weight_dvdl, dtype: int64
Lambda
1      989
2     1616
3     2780
4     2383
5     3024
6     2577
7     2234
8     2884
9     1301
10    1107
11    1426
12    1620
Name: weight_dvdl, dtype: int64
Lambda
1     1490
2      750
3      807
4     1224
5      658
6      642
7     1198
8      612
9      952
10     782
11     638
12     958
Name: weight_dvdl, dtype: int64


### Comparing TI sampling of the three microstates to the GaMD free energy profile areas

In [65]:

a1ub = v164_pmf_ub[(v164_pmf_ub["X"] > -120) & (v164_pmf_ub["X"] < -25)]["pop"].sum()
a2ub = v164_pmf_ub[(v164_pmf_ub["X"] > 0) & (v164_pmf_ub["X"] < 120)]["pop"].sum()
a3ub = v164_pmf_ub[(v164_pmf_ub["X"] > 120) | (v164_pmf_ub["X"] < -150)]["pop"].sum()

a1_prop_ub = a1ub/(a1ub + a2ub + a3ub)
a2_prop_ub = a2ub/(a1ub + a2ub + a3ub)
a3_prop_ub = a3ub/(a1ub + a2ub + a3ub)

print("GaMD pmf left hand state proportion: ")
print(round(a1_prop_ub, 4))
print("GaMD pmf middle state proportion: ")
print(round(a2_prop_ub, 4))
print("GaMD pmf right hand state proportion: ")
print(round(a3_prop_ub, 4))


ti1_ub = len(st1_ub)
ti2_ub = len(st2_ub)
ti3_ub = len(st3_ub)

print("TI left hand state proportion: ")
print(round(ti1_ub/(ti1_ub + ti2_ub + ti3_ub), 4))
print("TI middle hand state proportion: ")
print(round(ti2_ub/(ti1_ub + ti2_ub + ti3_ub), 4))
print("TI right hand state proportion: ")
print(round(ti3_ub/(ti1_ub + ti2_ub + ti3_ub), 4))


GaMD pmf left hand state proportion: 
0.0379
GaMD pmf middle state proportion: 
0.2124
GaMD pmf right hand state proportion: 
0.7497
TI left hand state proportion: 
0.2254
TI middle hand state proportion: 
0.5351
TI right hand state proportion: 
0.2394


### Recomputing unbound charging step dG and corrected charging step ddG

In [69]:
dG_corr_ub = a1_prop_ub * dG_st1_ub.sum() + a2_prop_ub * dG_st2_ub.sum() + a3_prop_ub * dG_st3_ub.sum()
ddG_corr = dG_corr - dG_corr_ub
print(ddG_corr)


-0.5515213208367982


#### Correction results

We are not adding in vdw step corrections here because the model $R^2$ did not convey a strong enough relationship between the geometric and energetic degrees of freedom. (see the R66G vdw step notebook).

With the correction based on the VL-V29 chi1/chi2 rotamer sampling, there is a modest improvement in prediction error.

In [68]:
dG_bd_crg = geom_dvdls_crg.groupby("Lambda").mean()["weight_dvdl"].sum()
dG_ubd_crg = geom_dvdls_crg_ub.groupby("Lambda").mean()["weight_dvdl"].sum()
ddG_crg = dG_bd_crg - dG_ubd_crg

dG_bd_vdw = geom_dvdls_vdw.groupby("Lambda").mean()["weight_dvdl"].sum()
dG_ubd_vdw = geom_dvdls_vdw_ub.groupby("Lambda").mean()["weight_dvdl"].sum()
ddG_vdw = dG_bd_vdw - dG_ubd_vdw

empirical_value = 0.22

print("Original ddG (crg step): ")
print(f"{round(ddG_crg, 4)} kcal/mol")

print("Original ddG (vdw step): ")
print(f"{round(ddG_vdw, 4)} kcal/mol")

print("Empirical value: ")
print(f"{empirical_value} kcal/mol")

orig_error = abs((ddG_crg + ddG_vdw) - empirical_value)

print("Original ddG error: ")
print(f"{round(orig_error, 4)} kcal/mol")

print()
print("Corrected ddG (crg step): ")
print(f"{round(ddG_corr, 4)} kcal/mol")
print("Corrected ddG (total): ")
print(f"{round(ddG_corr + ddG_vdw, 4)} kcal/mol")

corr_error = abs((ddG_corr + ddG_vdw) - empirical_value)
print("Corrected ddG error: ")
print(f"{round(corr_error, 4)} kcal/mol")


Original ddG (crg step): 
-0.8642 kcal/mol
Original ddG (vdw step): 
0.1575 kcal/mol
Empirical value: 
0.22 kcal/mol
Original ddG error: 
0.9266 kcal/mol

Corrected ddG (crg step): 
-0.5515 kcal/mol
Corrected ddG (total): 
-0.394 kcal/mol
Corrected ddG error: 
0.614 kcal/mol
